In [1]:
import sys
import os
import os.path as osp
import argparse
import numpy as np
import cv2
import json
import torch
from glob import glob
from tqdm import tqdm
import torchvision.transforms as transforms
from torch.nn.parallel.data_parallel import DataParallel
import torch.backends.cudnn as cudnn

sys.path.insert(0, osp.join('..', 'main'))
sys.path.insert(0, osp.join('..', 'data'))
sys.path.insert(0, osp.join('..', 'common'))
from config import cfg
from model_new import get_model
from utils.preprocessing import load_img, process_bbox, generate_patch_image, get_iou
from utils.vis import vis_keypoints_with_skeleton, save_obj, render_mesh_orthogonal
from utils.mano import mano

Fix shapedirs bug of MANO


In [2]:
cfg.set_args("0")
cudnn.benchmark = True

model_path = r"C:\Users\vladi\RP\InterWild\output\model_dump\snapshot_0.pth"
assert osp.exists(model_path), 'Cannot find model at ' + model_path
print('Load checkpoint from {}'.format(model_path))
model = get_model('test')
model = DataParallel(model).cuda()
ckpt = torch.load(model_path)
model.load_state_dict(ckpt['network'], strict=False)
model.eval()


>>> Using GPU: 0
Load checkpoint from C:\Users\vladi\RP\InterWild\output\model_dump\snapshot_0.pth


C:\Users\vladi\AppData\Local\Temp\ipykernel_34192\2820098046.py:9: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  ckpt = torch.load(model_path)


DataParallel(
  (module): Model(
    (body_backbone): ResNetBackbone(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu

In [4]:
ir_image_dir = r"C:\Users\vladi\RP\Research\IR_videos\every60thframe"
ir_image_paths = glob(osp.join(ir_image_dir, "*.jpg"))  # Assuming images are in .jpg forma
# Create a custom dataset for your infrared images
# Create a custom dataset for your infrared images
class InfraredDataset(torch.utils.data.Dataset):
    def __init__(self, image_paths, transform=None):
        self.image_paths = image_paths
        self.transform = transform

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        img_path = self.image_paths[idx]

        # Load and preprocess the image using InterWild's functions
        original_img = load_img(img_path)
        img_height, img_width = original_img.shape[:2]
        bbox = [0, 0, img_width, img_height]  # Use the entire image as the initial bbox
        bbox = process_bbox(bbox, img_width, img_height)
        img, img2bb_trans, bb2img_trans = generate_patch_image(original_img, bbox, 1.0, 0.0, False, cfg.input_img_shape)

        if self.transform:
            img = self.transform(img.astype(np.float32)) / 255
        
        return img

# Define transformations (match demo.py preprocessing)
transform = transforms.Compose([
    transforms.ToTensor(),
])

# Create dataset and dataloader
ir_dataset = InfraredDataset(ir_image_paths, transform=transform)
ir_dataloader = torch.utils.data.DataLoader(ir_dataset, batch_size=8, shuffle=True, num_workers=0)

In [5]:
our_dataset = InfraredDataset(r"C:\Users\vladi\RP\our_hands_dataset_labeled_previews\IR", transform=transform)
our_dataloader = torch.utils.data.DataLoader(ir_dataset, batch_size=8, shuffle=True, num_workers=0)

In [6]:
from adabn_utils import compute_bn_stats, replace_bn_stats, BatchNormStatHook
import os
os.environ['KMP_DUPLICATE_LIB_OK'] = 'True'

import random
import sys
import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F

from torch.utils.data import Dataset
from functools import partial

In [8]:
mms = []
for name, module in model.named_modules():
    if isinstance(module, torch.nn.BatchNorm2d):
        mms.append(module.momentum)

In [9]:
model.eval()
# Set BatchNorm layers to training mode
# Iterate through the dataloader
SetMomentum = 0.1
hook = BatchNormStatHook()
bn_stats_before = {}
with torch.no_grad():
    for name, module in model.named_modules():
        if isinstance(module, torch.nn.BatchNorm2d):
            print(module.running_mean)
            module.train()
            bn_stats_before[name] = {
                'mean': module.running_mean.clone(),
                'var': module.running_var.clone()
            }
            module.momentum = SetMomentum
            hook_handle = module.register_forward_hook(partial(hook, name=name))
            hook.hooks.append(hook_handle)
            

tensor([-1.5276e-01,  3.0978e-01, -5.7323e-01, -3.8754e-03,  1.0293e-02,
        -5.8371e-02,  5.5849e-03,  3.8458e-02, -6.6116e-03, -1.6909e-01,
        -6.1130e-03,  9.6764e-01,  2.2793e-02,  5.5423e-07, -2.6081e-02,
         1.2420e-03, -1.7786e-01,  1.1591e-02,  2.1375e-02,  5.7159e-02,
        -1.9285e-02, -2.5712e-02, -8.5726e-03, -3.5547e-01, -1.0663e-01,
        -6.2589e-01, -1.4629e-02, -4.9359e-02, -4.1940e-02, -5.4888e-01,
         2.4061e-02,  5.0177e-01,  1.2798e+00,  1.6024e-02, -2.9839e-02,
         1.8240e-01, -6.2011e-02,  1.6935e-01, -4.0524e-04,  1.6616e-02,
         1.0708e+00, -7.2555e-03,  1.3720e+00, -5.4510e-01, -1.4621e+00,
         1.7069e-02,  2.0080e-02, -2.2660e-01,  6.9033e-01, -2.7675e-02,
        -2.1856e-02,  2.5072e-02, -1.1766e+00, -3.2352e-02, -2.1061e-02,
         2.9101e-01,  1.0035e-01,  2.8949e-01, -8.9395e-01,  1.6913e-01,
         5.2732e-02, -2.5398e-02, -1.0118e+00, -4.2510e-03], device='cuda:0')
tensor([-7.6039e-01, -5.0628e-01,  4.1425e-01,

In [10]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
with torch.no_grad():
    for data in tqdm(our_dataloader):
        inputs = {'img': data.to(device)}
        targets = {}
        meta_info = {}
        # Forward pass (hook will accumulate statistics)
        model(inputs, targets, meta_info, "test")

  0%|          | 0/609 [00:00<?, ?it/s]

Here1
Here2
torch.Size([8, 64, 128, 96])
torch.Size([64, 128, 96])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 128, 64, 48])
torch.Size([128, 64, 48])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size

  0%|          | 1/609 [00:02<26:03,  2.57s/it]

torch.Size([16, 2048, 8, 8])
torch.Size([2048, 8, 8])
torch.Size([16, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([16, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([16, 2048, 8, 8])
torch.Size([2048, 8, 8])
torch.Size([16, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([16, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([16, 2048, 8, 8])
torch.Size([2048, 8, 8])
Here7
Here8


  0%|          | 2/609 [00:02<12:37,  1.25s/it]

...

Here1
Here2
torch.Size([8, 64, 128, 96])
torch.Size([64, 128, 96])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 128, 64, 48])
torch.Size([128, 64, 48])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size

100%|█████████▉| 608/609 [03:30<00:00,  3.00it/s]

Here1
Here2
torch.Size([8, 64, 128, 96])
torch.Size([64, 128, 96])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([8, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([8, 128, 64, 48])
torch.Size([128, 64, 48])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([8, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size

100%|██████████| 609/609 [03:31<00:00,  2.88it/s]

torch.Size([4, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([4, 2048, 8, 8])
torch.Size([2048, 8, 8])
torch.Size([4, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([4, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([4, 2048, 8, 8])
torch.Size([2048, 8, 8])
Here7
Here8


In [11]:
for layer_name, stats in hook.bn_stats.items():
        # Average the accumulated statistics
        mean = stats['mean'] / stats['count']
        var = stats['var'] / stats['count']
        hook.bn_stats[layer_name] = {'mean': mean, 'var': var}

In [12]:
hook.unhook()

In [13]:
# Write BN stats before and after to file
with open('adabnbeforeafter3.txt', 'w') as f:
    for layer_name in hook.bn_stats:
        if layer_name in bn_stats_before:
            f.write(f"Layer: {layer_name}\n")
            f.write("Before:\n")
            f.write(f"Mean: {bn_stats_before[layer_name]['mean']}\n")
            if 'var' in bn_stats_before[layer_name]:
                f.write(f"Var: {bn_stats_before[layer_name]['var']}\n")
            f.write("\nAfter:\n") 
            f.write(f"Mean: {hook.bn_stats[layer_name]['mean']}\n")
            if 'var' in hook.bn_stats[layer_name]:
                f.write(f"Var: {hook.bn_stats[layer_name]['var']}\n")
            f.write("\n" + "="*80 + "\n\n")

In [14]:
# Open file to save prints
with open('bn_stats_output3.txt', 'w') as f:
    # Redirect prints to file
    import sys
    original_stdout = sys.stdout
    sys.stdout = f
    
    replace_bn_stats(model, hook.bn_stats, ratio=0.5)
    sys.stdout = original_stdout

In [ ]:
predictions = []
# Process each image
model.eval()
for img_path in ir_image_paths:
   # Load and process image (your existing code)
   original_img = load_img(img_path)
   img_height, img_width = original_img.shape[:2]
   bbox = [0, 0, img_width, img_height]
   bbox = process_bbox(bbox, img_width, img_height)
   img, img2bb_trans, bb2img_trans = generate_patch_image(original_img, bbox, 1.0, 0.0, False, cfg.input_img_shape)
   transform = transforms.ToTensor()
   img = transform(img.astype(np.float32))/255
   img = img.cuda()[None,:,:,:]
    # Forward pass
   inputs = {'img': img}
   targets = {}
   meta_info = {}
   with torch.no_grad():
       out = model(inputs, targets, meta_info, 'test')
    # Get predictions for both hands
   prediction = {
       "image": os.path.basename(img_path),
       "width": int(img_width),
       "height": int(img_height),
       "landmarks": [],
       "normalized": True
   }
   
   for hand in ('left', 'right'):
       # Get joint coordinates
       joint_img = out[hand[0] + 'joint_img'].cpu().numpy()[0]
       joint_img_xy1 = np.concatenate((joint_img[:,:2], np.ones_like(joint_img[:,:1])),1)
       joint_img = np.dot(bb2img_trans, joint_img_xy1.transpose(1,0)).transpose(1,0)
       
       # Normalize and format coordinates
       hand_points = []
       for point in joint_img:
           hand_points.append(normalize_coords(point[0], point[1], img_width, img_height))
       
       prediction["landmarks"].append(hand_points)
   
   predictions.append(prediction)